In [1]:
import pandas as pd
from collections import defaultdict

# -------------------------------
# Часть 1. Предобработка данных
# -------------------------------
def preprocess_data(df):
    transactions = []    
    selected_columns = ['Timestamp', 'Source IP', 'Source Port', 'Destination IP', 'Destination Port', 'Protocol', 'Label']
    for index, row in df.iterrows():
        transaction = []
        for col in selected_columns:
            value = str(row[col])
            item = f"{col}:{value}"
            transaction.append(item)
        transactions.append(transaction)
    return transactions


In [2]:
# -------------------------------
# Часть 2. Построение FP-дерева (MDFP)
# -------------------------------
class FPNode:
    def __init__(self, item, count, parent):
        self.item = item          # Например, "Protocol:TCP"
        self.count = count        # Подсчет вхождений
        self.parent = parent      # Ссылка на родительский узел
        self.children = {}        # Дочерние узлы: ключ – имя элемента, значение – объект FPNode
        self.node_link = None     # Ссылка на следующий узел с таким же элементом

    def increment(self, count):
        self.count += count

def update_header(node, target_node):
    while node.node_link is not None:
        node = node.node_link
    node.node_link = target_node

def update_tree(items, tree, header_table, count):
    first_item = items[0]
    if first_item in tree.children:
        tree.children[first_item].increment(count)
    else:
        new_node = FPNode(first_item, count, tree)
        tree.children[first_item] = new_node
        if header_table[first_item][1] is None:
            header_table[first_item][1] = new_node
        else:
            update_header(header_table[first_item][1], new_node)
    if len(items) > 1:
        update_tree(items[1:], tree.children[first_item], header_table, count)

def create_fp_tree(transactions, min_support):
    freq = {}
    for transaction in transactions:
        for item in transaction:
            freq[item] = freq.get(item, 0) + 1
    freq = {item: count for item, count in freq.items() if count >= min_support}
    if len(freq) == 0:
        return None, None

    header_table = {item: [count, None] for item, count in freq.items()}
    root = FPNode('Null', 1, None)
    
    for transaction in transactions:
        transaction_items = [item for item in transaction if item in freq]
        if len(transaction_items) > 0:
            sorted_items = sorted(transaction_items, key=lambda item: header_table[item][0], reverse=True)
            update_tree(sorted_items, root, header_table, 1)
    return root, header_table

def ascend_fp_tree(node):
    path = []
    while node.parent is not None and node.parent.item != 'Null':
        node = node.parent
        path.append(node.item)
    return path

def find_prefix_paths(base_item, header_table):
    conditional_patterns = {}
    node = header_table[base_item][1]
    while node is not None:
        prefix_path = ascend_fp_tree(node)
        if len(prefix_path) > 0:
            conditional_patterns[frozenset(prefix_path)] = node.count
        node = node.node_link
    return conditional_patterns

def mine_fp_tree(tree, header_table, min_support, pre_fix, frequent_itemsets):
    sorted_items = sorted(header_table.items(), key=lambda x: x[1][0])
    for base_item, base_info in sorted_items:
        new_freq_set = pre_fix.copy()
        new_freq_set.add(base_item)
        frequent_itemsets[frozenset(new_freq_set)] = base_info[0]
        conditional_pattern_bases = find_prefix_paths(base_item, header_table)
        conditional_transactions = []
        for path, count in conditional_pattern_bases.items():
            transaction = list(path)
            for _ in range(count):
                conditional_transactions.append(transaction)
        if len(conditional_transactions) > 0:
            conditional_tree, conditional_header = create_fp_tree(conditional_transactions, min_support)
            if conditional_header is not None:
                mine_fp_tree(conditional_tree, conditional_header, min_support, new_freq_set, frequent_itemsets)


In [3]:
# -------------------------------
# Часть 3. Построение COFI-дерева (g-cofi-tree)
# -------------------------------
# Класс COFINode с дополнительным счетчиком участия
class COFINode:
    def __init__(self, item, count, parent):
        self.item = item                # Имя элемента (например, "Protocol:6")
        self.count = count              # Подсчет вхождений
        self.parent = parent            # Родительский узел
        self.children = {}              # Дочерние узлы (словарь: ключ – имя элемента, значение – COFINode)
        self.node_link = None           # Ссылка на следующий узел с таким же элементом
        self.participation_counter = 0  # Дополнительный счетчик участия

    def increment(self, count):
        self.count += count

def update_cofi_tree(items, tree, header_table, count):
    first_item = items[0]
    if first_item in tree.children:
        tree.children[first_item].increment(count)
    else:
        new_node = COFINode(first_item, count, tree)
        tree.children[first_item] = new_node
        if header_table[first_item][1] is None:
            header_table[first_item][1] = new_node
        else:
            current = header_table[first_item][1]
            while current.node_link is not None:
                current = current.node_link
            current.node_link = new_node
    if len(items) > 1:
        update_cofi_tree(items[1:], tree.children[first_item], header_table, count)

def create_cofi_tree(transactions, min_support):
    freq = {}
    for transaction in transactions:
        for item in transaction:
            freq[item] = freq.get(item, 0) + 1
    freq = {item: count for item, count in freq.items() if count >= min_support}
    if len(freq) == 0:
        return None, None
    header_table = {item: [count, None] for item, count in freq.items()}
    root = COFINode('Null', 1, None)
    
    for transaction in transactions:
        transaction_items = [item for item in transaction if item in freq]
        if len(transaction_items) > 0:
            sorted_items = sorted(transaction_items, key=lambda item: header_table[item][0], reverse=True)
            update_cofi_tree(sorted_items, root, header_table, 1)
    return root, header_table

def build_cofi_tree_for_item(base_item, fp_header, min_support):
    conditional_patterns = find_prefix_paths(base_item, fp_header)
    cofi_transactions = []
    for path, count in conditional_patterns.items():
        transaction = list(path)
        for _ in range(count):
            cofi_transactions.append(transaction)
    return create_cofi_tree(cofi_transactions, min_support)

def mine_cofi_tree(tree, header_table, min_support, pre_fix, cofi_patterns):
    sorted_items = sorted(header_table.items(), key=lambda x: x[1][0])
    for base_item, base_info in sorted_items:
        new_freq_set = pre_fix.copy()
        new_freq_set.add(base_item)
        cofi_patterns[frozenset(new_freq_set)] = base_info[0]
        conditional_patterns = find_prefix_paths(base_item, header_table)
        conditional_transactions = []
        for path, count in conditional_patterns.items():
            transaction = list(path)
            for _ in range(count):
                conditional_transactions.append(transaction)
        if len(conditional_transactions) > 0:
            conditional_tree, conditional_header = create_cofi_tree(conditional_transactions, min_support)
            if conditional_header is not None:
                mine_cofi_tree(conditional_tree, conditional_header, min_support, new_freq_set, cofi_patterns)


In [4]:
# -------------------------------
# Часть 4. Реализация структуры SD для объединения баз частых путей
# -------------------------------
def build_sd_structure(cofi_patterns, min_support):
    """
    Функция группирует найденные частые пути (cofi_patterns) по их длине
    и пересчитывает поддержку: если набор является подмножеством другого,
    его поддержка увеличивается на поддержку того, в котором он содержится.
    
    :param cofi_patterns: Словарь, где ключ – frozenset элементов, значение – поддержка.
    :param min_support: Порог поддержки.
    :return: Итоговый словарь частых наборов после обработки структурой SD.
    """
    # Группировка по длине набора
    sd_segments = {}
    for pattern, support in cofi_patterns.items():
        length = len(pattern)
        sd_segments.setdefault(length, []).append((pattern, support))
    
    # Итерируем по сегментам: для каждого набора из сегмента меньшей длины
    # ищем наборы в сегментах с большей длиной, которые содержат его.
    updated_patterns = {}
    for length in sorted(sd_segments.keys()):
        for pattern, support in sd_segments[length]:
            updated_support = support
            for longer_length in sorted(sd_segments.keys()):
                if longer_length > length:
                    for longer_pattern, longer_support in sd_segments[longer_length]:
                        if pattern.issubset(longer_pattern):
                            updated_support += longer_support
            updated_patterns[pattern] = updated_support
    # Оставляем только те наборы, чья обновленная поддержка >= min_support
    final_patterns = {pattern: sup for pattern, sup in updated_patterns.items() if sup >= min_support}
    return final_patterns


In [5]:
# -------------------------------
# Часть 5. Запуск всей цепочки: от данных до SD структуры
# -------------------------------

# Загрузка данных и предобработка
df = pd.read_csv(r'C:\Users\Гребенников Матвей\Desktop\Диплом\Диплом\GeneratedLabelledFlows\TrafficLabelling\Monday-WorkingHours.pcap_ISCX.csv')
df.columns = df.columns.str.strip()
transactions = preprocess_data(df)

min_support = 10  # минимальный порог поддержки

# Построение FP-дерева (MDFP)
fp_tree, header_table = create_fp_tree(transactions, min_support)
if fp_tree is None:
    print("Нет частых элементов, удовлетворяющих минимальному порогу поддержки.")
else:
    frequent_itemsets = {}
    mine_fp_tree(fp_tree, header_table, min_support, set(), frequent_itemsets)
    
    print("Найденные частые наборы (MDFP):")
    for itemset, support in frequent_itemsets.items():
        print(set(itemset), "поддержка:", support)

    # Выбираем базовый элемент для построения COFI-дерева, например "Protocol:6"
    # Допустим, вы хотите обработать несколько базовых элементов:
base_items = ["Protocol:6", "Destination Port:53", "Label:BENIGN"]

all_cofi_patterns = {}
for base_item in base_items:
    if base_item in header_table:
        cofi_tree, cofi_header = build_cofi_tree_for_item(base_item, header_table, min_support)
        if cofi_tree and cofi_header:
            cofi_patterns = {}
            mine_cofi_tree(cofi_tree, cofi_header, min_support, pre_fix=set([base_item]), cofi_patterns=cofi_patterns)
            print(f"\nЧастые наборы из COFI-дерева для {base_item}:")
            for itemset, support in sorted(cofi_patterns.items(), key=lambda x: x[1], reverse=True):
                print(set(itemset), "поддержка:", support)
            # Объединяем все полученные наборы
            all_cofi_patterns.update(cofi_patterns)
        else:
            print(f"\nНет условных транзакций для {base_item} с поддержкой >= {min_support}.")
    else:
        print(f"\nЭлемент {base_item} не найден в FP-дереве.")

print("\n--- Применение структуры SD ко всем полученным наборов ---")
sd_patterns = build_sd_structure(all_cofi_patterns, min_support)
for pattern, support in sorted(sd_patterns.items(), key=lambda x: x[1], reverse=True):
    print(set(pattern), "поддержка:", support)


Найденные частые наборы (MDFP):
{'Source IP:23.217.36.24'} поддержка: 10
{'Source IP:23.217.36.24', 'Label:BENIGN'} поддержка: 10
{'Source IP:23.217.36.24', 'Protocol:6'} поддержка: 10
{'Source IP:23.217.36.24', 'Label:BENIGN', 'Protocol:6'} поддержка: 10
{'Source IP:23.217.36.24', 'Source Port:443'} поддержка: 10
{'Source IP:23.217.36.24', 'Label:BENIGN', 'Source Port:443'} поддержка: 10
{'Timestamp:03/07/2017 08:59:05'} поддержка: 10
{'Label:BENIGN', 'Timestamp:03/07/2017 08:59:05'} поддержка: 10
{'Source IP:192.168.10.25', 'Timestamp:03/07/2017 08:59:05'} поддержка: 10
{'Label:BENIGN', 'Source IP:192.168.10.25', 'Timestamp:03/07/2017 08:59:05'} поддержка: 10
{'Destination IP:192.168.10.3', 'Timestamp:03/07/2017 08:59:05'} поддержка: 10
{'Label:BENIGN', 'Destination IP:192.168.10.3', 'Timestamp:03/07/2017 08:59:05'} поддержка: 10
{'Destination IP:192.168.10.3', 'Source IP:192.168.10.25', 'Timestamp:03/07/2017 08:59:05'} поддержка: 10
{'Label:BENIGN', 'Destination IP:192.168.10.3', 'S

IOPub data rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_data_rate_limit`.

Current values:
ServerApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
ServerApp.rate_limit_window=3.0 (secs)



 10
{'Source IP:192.168.10.3', 'Timestamp:03/07/2017 09:39:00', 'Destination Port:53'} поддержка: 10
{'Source IP:192.168.10.3', 'Label:BENIGN', 'Timestamp:03/07/2017 09:39:00', 'Destination Port:53'} поддержка: 10
{'Source IP:192.168.10.3', 'Protocol:17', 'Timestamp:03/07/2017 09:39:00', 'Destination Port:53'} поддержка: 10
{'Source IP:192.168.10.3', 'Label:BENIGN', 'Timestamp:03/07/2017 09:39:00', 'Protocol:17', 'Destination Port:53'} поддержка: 10
{'Destination IP:192.168.10.1', 'Timestamp:03/07/2017 09:39:00'} поддержка: 10
{'Source IP:192.168.10.3', 'Destination IP:192.168.10.1', 'Timestamp:03/07/2017 09:39:00'} поддержка: 10
{'Label:BENIGN', 'Destination IP:192.168.10.1', 'Timestamp:03/07/2017 09:39:00'} поддержка: 10
{'Source IP:192.168.10.3', 'Label:BENIGN', 'Destination IP:192.168.10.1', 'Timestamp:03/07/2017 09:39:00'} поддержка: 10
{'Protocol:17', 'Destination IP:192.168.10.1', 'Timestamp:03/07/2017 09:39:00'} поддержка: 10
{'Source IP:192.168.10.3', 'Protocol:17', 'Destinati

IOPub data rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_data_rate_limit`.

Current values:
ServerApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
ServerApp.rate_limit_window=3.0 (secs)



43
{'Timestamp:03/07/2017 02:09:23'} поддержка: 43
{'Timestamp:03/07/2017 02:09:23', 'Source Port:443'} поддержка: 11
{'Timestamp:03/07/2017 02:09:23', 'Source Port:443', 'Label:BENIGN'} поддержка: 11
{'Timestamp:03/07/2017 02:09:23', 'Source Port:443', 'Protocol:6'} поддержка: 11
{'Timestamp:03/07/2017 02:09:23', 'Source Port:443', 'Label:BENIGN', 'Protocol:6'} поддержка: 11
{'Timestamp:03/07/2017 02:09:23', 'Destination IP:192.168.10.8'} поддержка: 11
{'Timestamp:03/07/2017 02:09:23', 'Source Port:443', 'Destination IP:192.168.10.8'} поддержка: 11
{'Timestamp:03/07/2017 02:09:23', 'Destination IP:192.168.10.8', 'Label:BENIGN'} поддержка: 11
{'Timestamp:03/07/2017 02:09:23', 'Source Port:443', 'Destination IP:192.168.10.8', 'Label:BENIGN'} поддержка: 11
{'Timestamp:03/07/2017 02:09:23', 'Destination IP:192.168.10.8', 'Protocol:6'} поддержка: 11
{'Timestamp:03/07/2017 02:09:23', 'Source Port:443', 'Destination IP:192.168.10.8', 'Protocol:6'} поддержка: 11
{'Timestamp:03/07/2017 02:09:2

IOPub data rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_data_rate_limit`.

Current values:
ServerApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
ServerApp.rate_limit_window=3.0 (secs)



 40
{'Destination IP:192.168.10.3', 'Timestamp:03/07/2017 04:53:10', 'Source IP:192.168.10.15'} поддержка: 40
{'Destination IP:192.168.10.3', 'Label:BENIGN', 'Timestamp:03/07/2017 04:53:10'} поддержка: 40
{'Destination IP:192.168.10.3', 'Label:BENIGN', 'Timestamp:03/07/2017 04:53:10', 'Source IP:192.168.10.15'} поддержка: 40
{'Destination IP:192.168.10.3', 'Protocol:17', 'Timestamp:03/07/2017 04:53:10'} поддержка: 40
{'Destination IP:192.168.10.3', 'Protocol:17', 'Timestamp:03/07/2017 04:53:10', 'Label:BENIGN'} поддержка: 40
{'Destination IP:192.168.10.3', 'Protocol:17', 'Timestamp:03/07/2017 04:53:10', 'Source IP:192.168.10.15'} поддержка: 40
{'Label:BENIGN', 'Timestamp:03/07/2017 04:53:10', 'Destination IP:192.168.10.3', 'Protocol:17', 'Source IP:192.168.10.15'} поддержка: 40
{'Destination IP:192.168.10.3', 'Timestamp:03/07/2017 04:53:10', 'Destination Port:53'} поддержка: 40
{'Destination IP:192.168.10.3', 'Label:BENIGN', 'Timestamp:03/07/2017 04:53:10', 'Destination Port:53'} подде

IOPub data rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_data_rate_limit`.

Current values:
ServerApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
ServerApp.rate_limit_window=3.0 (secs)



{'Source IP:172.217.12.130', 'Source Port:443', 'Destination IP:192.168.10.51', 'Protocol:6'} поддержка: 13
{'Source IP:172.217.12.130', 'Label:BENIGN', 'Protocol:6', 'Source Port:443', 'Destination IP:192.168.10.51'} поддержка: 13
{'Source IP:172.217.12.130', 'Label:BENIGN', 'Destination IP:192.168.10.51'} поддержка: 17
{'Source IP:172.217.12.130', 'Destination IP:192.168.10.51', 'Protocol:6'} поддержка: 17
{'Source IP:172.217.12.130', 'Label:BENIGN', 'Destination IP:192.168.10.51', 'Protocol:6'} поддержка: 17
{'Source IP:172.217.12.130', 'Source Port:80'} поддержка: 29
{'Source IP:172.217.12.130', 'Destination IP:192.168.10.25', 'Source Port:80'} поддержка: 14
{'Source IP:172.217.12.130', 'Label:BENIGN', 'Destination IP:192.168.10.25', 'Source Port:80'} поддержка: 14
{'Source IP:172.217.12.130', 'Destination IP:192.168.10.25', 'Source Port:80', 'Protocol:6'} поддержка: 14
{'Source IP:172.217.12.130', 'Destination IP:192.168.10.25', 'Label:BENIGN', 'Protocol:6', 'Source Port:80'} подд